<a href="https://colab.research.google.com/github/Titanic-minds-group-14/Kaggle-challenge-group-14/blob/main/spaceship_titanic_1new.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Kaggle Challenge - SpaceShip Titanic
  Group-14 (Titanic Minds)

## Necessary Imports and Setup

In [ ]:
!pip install catboost

In [ ]:
# Core packages
import pandas as pd
import numpy as np
import warnings
warnings.filterwarnings('ignore')

# Visualization
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from itertools import cycle

# Sklearn: Preprocessing & pipeline
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.preprocessing import  OneHotEncoder, StandardScaler
from sklearn.impute import SimpleImputer
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline

# Sklearn: Models
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier

# Sklearn: Metrics
from sklearn.metrics import (
    accuracy_score, classification_report, confusion_matrix,
    roc_auc_score, roc_curve, precision_recall_curve, auc
)

# Advanced models
from xgboost import XGBClassifier
from catboost import CatBoostClassifier

# Density estimation (for KDE plots if needed)
from scipy.stats import gaussian_kde

# Google Colab file handling
from google.colab import files


## Data Loading

In [ ]:
def load_and_inspect_data(train_url, test_url):
    """
    Loads train and test CSVs from Github URLs and displays basic shape and preview.

    Parameters:
    train_url: str, URL to the train dataset
    test_url: str, URL to the test dataset

    Returns:
    train_df: pd.DataFrame
    test_df: pd.DataFrame
    """
    # Load data
    train_df = pd.read_csv(train_url)
    test_df = pd.read_csv(test_url)

    # Display shapes and first few rows
    print(f"Train shape: {train_df.shape}")
    print("\nTrain sample:")
    display(train_df.head())

    print(f"\nTest shape: {test_df.shape}")
    print("\nTest sample:")
    display(test_df.head())

    return train_df, test_df


In [ ]:
train_url = 'https://raw.githubusercontent.com/Titanic-minds-group-14/Kaggle-challenge-group-14-/refs/heads/main/Data/train.csv'
test_url = 'https://raw.githubusercontent.com/Titanic-minds-group-14/Kaggle-challenge-group-14-/refs/heads/main/Data/test.csv'

train_df, test_df = load_and_inspect_data(train_url, test_url)


Train shape: (8693, 14)

Train sample:


PassengerId HomePlanet CryoSleep  Cabin  Destination   Age    VIP  \
0     0001_01     Europa     False  B/0/P  TRAPPIST-1e  39.0  False   
1     0002_01      Earth     False  F/0/S  TRAPPIST-1e  24.0  False   
2     0003_01     Europa     False  A/0/S  TRAPPIST-1e  58.0   True   
3     0003_02     Europa     False  A/0/S  TRAPPIST-1e  33.0  False   
4     0004_01      Earth     False  F/1/S  TRAPPIST-1e  16.0  False   

   RoomService  FoodCourt  ShoppingMall     Spa  VRDeck               Name  \
0          0.0        0.0           0.0     0.0     0.0    Maham Ofracculy   
1        109.0        9.0          25.0   549.0    44.0       Juanna Vines   
2         43.0     3576.0           0.0  6715.0    49.0      Altark Susent   
3          0.0     1283.0         371.0  3329.0   193.0       Solam Susent   
4        303.0       70.0         151.0   565.0     2.0  Willy Santantines   

   Transported  
0        False  
1         True  
2        False  
3        False  
4         True


Test shape: (4277, 13)

Test sample:


PassengerId HomePlanet CryoSleep  Cabin  Destination   Age    VIP  \
0     0013_01      Earth      True  G/3/S  TRAPPIST-1e  27.0  False   
1     0018_01      Earth     False  F/4/S  TRAPPIST-1e  19.0  False   
2     0019_01     Europa      True  C/0/S  55 Cancri e  31.0  False   
3     0021_01     Europa     False  C/1/S  TRAPPIST-1e  38.0  False   
4     0023_01      Earth     False  F/5/S  TRAPPIST-1e  20.0  False   

   RoomService  FoodCourt  ShoppingMall     Spa  VRDeck              Name  
0          0.0        0.0           0.0     0.0     0.0   Nelly Carsoning  
1          0.0        9.0           0.0  2823.0     0.0    Lerome Peckers  
2          0.0        0.0           0.0     0.0     0.0   Sabih Unhearfus  
3          0.0     6652.0           0.0   181.0   585.0  Meratz Caltilter  
4         10.0        0.0         635.0     0.0     0.0   Brence Harperez

In [ ]:
def display_dataset_info(train_df, test_df):
    """
    Function to display basic info (column names, non-null counts, data types)
    of train and test DataFrames.

    Parameters:
    train_df: pd.DataFrame, training dataset
    test_df: pd.DataFrame, testing dataset
    """
    print("Train DataFrame Info:")
    train_df.info()
    print("\n" + "-"*50 + "\n")
    print("Test DataFrame Info:")
    test_df.info()


In [ ]:
display_dataset_info(train_df, test_df)


Train DataFrame Info:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8693 entries, 0 to 8692
Data columns (total 14 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   PassengerId   8693 non-null   object 
 1   HomePlanet    8492 non-null   object 
 2   CryoSleep     8476 non-null   object 
 3   Cabin         8494 non-null   object 
 4   Destination   8511 non-null   object 
 5   Age           8514 non-null   float64
 6   VIP           8490 non-null   object 
 7   RoomService   8512 non-null   float64
 8   FoodCourt     8510 non-null   float64
 9   ShoppingMall  8485 non-null   float64
 10  Spa           8510 non-null   float64
 11  VRDeck        8505 non-null   float64
 12  Name          8493 non-null   object 
 13  Transported   8693 non-null   bool   
dtypes: bool(1), float64(6), object(7)
memory usage: 891.5+ KB

--------------------------------------------------

Test DataFrame Info:
<class 'pandas.core.frame.DataFrame'>
RangeInd

In [ ]:
def missing_data_report(df, name):
  missing_count = df.isnull().sum()
  missing_percent = 100 * missing_count / len(df)
  missing_table = pd.DataFrame({
      'Missing Count': missing_count,
      'Missing Percent (%)': missing_percent
  })
  missing_table = missing_table[missing_table.iloc[:, 0] != 0].sort_values(
      'Missing Percent (%)', ascending=False
  ).round(1)
  print(f"\n{name} - Missing Values:")
  display(missing_table)


missing_data_report(train_df, "Train")
missing_data_report(test_df, "Test")



Train - Missing Values:


Missing Count  Missing Percent (%)
CryoSleep               217                  2.5
ShoppingMall            208                  2.4
VIP                     203                  2.3
HomePlanet              201                  2.3
Name                    200                  2.3
Cabin                   199                  2.3
VRDeck                  188                  2.2
FoodCourt               183                  2.1
Spa                     183                  2.1
Destination             182                  2.1
RoomService             181                  2.1
Age                     179                  2.1


Test - Missing Values:


Missing Count  Missing Percent (%)
FoodCourt               106                  2.5
Spa                     101                  2.4
Cabin                   100                  2.3
ShoppingMall             98                  2.3
Name                     94                  2.2
VIP                      93                  2.2
CryoSleep                93                  2.2
Destination              92                  2.2
Age                      91                  2.1
HomePlanet               87                  2.0
RoomService              82                  1.9
VRDeck                   80                  1.9

In [ ]:
def check_duplicates(train_df, test_df):
    """
    Function to check and print the number of duplicate rows in train and test datasets.

    Parameters:
     train_df: pd.DataFrame, training dataset
     test_df: pd.DataFrame, testing dataset
    """
    print("Checking for duplicates:")
    train_dupes = train_df.duplicated().sum()
    test_dupes = test_df.duplicated().sum()
    print(f"Train duplicates: {train_dupes}")
    print(f"Test duplicates: {test_dupes}")


In [ ]:
check_duplicates(train_df, test_df)


Checking for duplicates:
Train duplicates: 0
Test duplicates: 0


In [ ]:
def check_cardinality(train_df, test_df):
    """
    Function to print the cardinality (number of unique values) of each feature
    in the train and test datasets.

    Parameters:
     train_df: pd.DataFrame, training dataset
     test_df: pd.DataFrame, testing dataset
    """
    print("Cardinality of features in Train dataset:")
    print(train_df.nunique())

    print("\nCardinality of features in Test dataset:")
    print(test_df.nunique())


In [ ]:
check_cardinality(train_df, test_df)


Cardinality of features in Train dataset:
PassengerId     8693
HomePlanet         3
CryoSleep          2
Cabin           6560
Destination        3
Age               80
VIP                2
RoomService     1273
FoodCourt       1507
ShoppingMall    1115
Spa             1327
VRDeck          1306
Name            8473
Transported        2
dtype: int64

Cardinality of features in Test dataset:
PassengerId     4277
HomePlanet         3
CryoSleep          2
Cabin           3265
Destination        3
Age               79
VIP                2
RoomService      842
FoodCourt        902
ShoppingMall     715
Spa              833
VRDeck           796
Name            4176
dtype: int64


In [ ]:
train_df.describe().T

count        mean          std  min   25%   50%   75%      max
Age           8514.0   28.827930    14.489021  0.0  19.0  27.0  38.0     79.0
RoomService   8512.0  224.687617   666.717663  0.0   0.0   0.0  47.0  14327.0
FoodCourt     8510.0  458.077203  1611.489240  0.0   0.0   0.0  76.0  29813.0
ShoppingMall  8485.0  173.729169   604.696458  0.0   0.0   0.0  27.0  23492.0
Spa           8510.0  311.138778  1136.705535  0.0   0.0   0.0  59.0  22408.0
VRDeck        8505.0  304.854791  1145.717189  0.0   0.0   0.0  46.0  24133.0

In [ ]:
test_df.describe().T

count        mean          std  min   25%   50%   75%      max
Age           4186.0   28.658146    14.179072  0.0  19.0  26.0  37.0     79.0
RoomService   4195.0  219.266269   607.011289  0.0   0.0   0.0  53.0  11567.0
FoodCourt     4171.0  439.484296  1527.663045  0.0   0.0   0.0  78.0  25273.0
ShoppingMall  4179.0  177.295525   560.821123  0.0   0.0   0.0  33.0   8292.0
Spa           4176.0  303.052443  1117.186015  0.0   0.0   0.0  50.0  19844.0
VRDeck        4197.0  310.710031  1246.994742  0.0   0.0   0.0  36.0  22272.0

# Identifying the Numerical Colunms and Categorical Colunms in the dataset


In [ ]:
def summarize_column_types(train_df):
    """
    Print a summary of numerical and categorical columns in a DataFrame.

    Args:
        train_df (pandas.DataFrame): Input DataFrame to analyze.

    Returns:
        None: Prints counts and names of numerical and categorical columns.
    """
    # To Identify numerical and categorical columns
    numerical_cols = train_df.select_dtypes(include=['int64', 'float64']).columns.tolist()
    categorical_cols = train_df.select_dtypes(include=['object', 'category', 'bool']).columns.tolist()

    # To Count of numerical and categorical columns
    num_numerical = len(numerical_cols)
    num_categorical = len(categorical_cols)

    # Print the results in a professional format
    print(" Dataset Column Type Summary ")
    print(f"Total Numerical Columns: {num_numerical}")
    print("Numerical Columns:")
    for col in numerical_cols:
        print(f"   {col}")

    print(f"\nTotal Categorical Columns: {num_categorical}")
    print("Categorical Columns:")
    for col in categorical_cols:
        print(f"   {col}")

    return numerical_cols, categorical_cols

In [ ]:
summarize_column_types(train_df)

 Dataset Column Type Summary 
Total Numerical Columns: 6
Numerical Columns:
   Age
   RoomService
   FoodCourt
   ShoppingMall
   Spa
   VRDeck

Total Categorical Columns: 8
Categorical Columns:
   PassengerId
   HomePlanet
   CryoSleep
   Cabin
   Destination
   VIP
   Name
   Transported


(['Age', 'RoomService', 'FoodCourt', 'ShoppingMall', 'Spa', 'VRDeck'],
 ['PassengerId',
  'HomePlanet',
  'CryoSleep',
  'Cabin',
  'Destination',
  'VIP',
  'Name',
  'Transported'])

# Total Missing Value Visualization per feature

In [ ]:
def plot_missing_data(train_df):
    """
    Plot a bar chart of missing values per feature in a DataFrame.

    Args:
        train_df (pandas.DataFrame): Input DataFrame to analyze for missing values.

    Returns:
        None: Displays a Plotly bar plot of features with missing values.
    """
    # Calculating missing values per feature
    missing_data = train_df.isnull().sum().reset_index()
    missing_data.columns = ['Feature', 'Missing Count']
    missing_data = missing_data[missing_data['Missing Count'] > 0]

    # Sort by missing count for better visualization
    missing_data = missing_data.sort_values(by='Missing Count', ascending=False)

    # Creating enhanced bar plot
    fig = px.bar(
        missing_data,
        x='Feature',
        y='Missing Count',
        color='Missing Count',
        color_continuous_scale='Reds',
        title=' Missing Data Overview by Feature',
        text='Missing Count'
    )

    # Update layout and formatting
    fig.update_layout(
        xaxis_title=' Feature Name',
        yaxis_title=' Number of Missing Values',
        xaxis_tickangle=-45,
        plot_bgcolor='rgba(240,240,240,0.95)',
        paper_bgcolor='white',
        font=dict(size=14, family='Arial'),
        title_font=dict(size=20),
        margin=dict(l=60, r=30, t=80, b=120),
        height=600
    )

    # Customize text inside bars
    fig.update_traces(
        texttemplate='%{text}',
        textposition='outside'
    )

    fig.show()


In [ ]:
plot_missing_data(train_df)

# Target class Distribution

In [ ]:
def plot_transported_distribution(train_df):
    """
    Plot an interactive histogram of the 'Transported' column.

    Args:
        train_df (pandas.DataFrame): Input DataFrame containing 'Transported' column.

    Returns:
        None: Displays an interactive Plotly bar chart of the 'Transported' class distribution.
    """
    fig = px.histogram(
        train_df,
        x='Transported',
        color='Transported',
        title='Transported Class Distribution',
        color_discrete_sequence=px.colors.qualitative.Set2
    )

    fig.update_layout(
        xaxis_title='Transported',
        yaxis_title='Count',
        showlegend=False,
        bargap=0.2
    )

    fig.show()


In [ ]:
plot_transported_distribution(train_df)


#Feature Distribution Summary

In [ ]:
def plot_feature_distribution(train_df):
    """
    Plot an interactive pie chart of numerical vs. categorical feature distribution.

    Args:
        train_df (pandas.DataFrame): Input DataFrame to analyze for feature types.

    Returns:
        None: Displays a Plotly pie chart showing the proportion of numerical vs. categorical features.
    """
    # Separate columns by type
    numerical_cols = train_df.select_dtypes(include=['float64', 'int64']).columns.tolist()
    categorical_cols = train_df.select_dtypes(include=['object', 'bool', 'category']).columns.tolist()

    # Count features
    type_labels = ['Numerical', 'Categorical']
    type_counts = [len(numerical_cols), len(categorical_cols)]

    # Create Plotly pie chart
    fig = go.Figure(data=[go.Pie(
        labels=type_labels,
        values=type_counts,
        marker=dict(colors=px.colors.qualitative.Set2),
        textinfo='percent+label'
    )])

    fig.update_layout(
        title='Feature Distribution: Numerical vs Categorical',
        showlegend=True,
        legend=dict(x=0, y=0, traceorder='normal', orientation='h'),
    )

    fig.show()


In [ ]:
plot_feature_distribution(train_df)

# Detailed Exploratory Data Analysis (EDA)


In [ ]:
def analyze_outliers_iqr(train_df, numerical_cols):
    """
    Analyze outliers in numerical columns using the IQR (interquartile range) method and display a summary table.

    Args:
        train_df (pandas.DataFrame): Input DataFrame containing numerical columns.
        numerical_cols (list): List of numerical column names to analyze.

    Returns:
        None: Prints a sorted table summarizing outlier counts and bounds for each feature.
    """
    outlier_summary = []

    for col in numerical_cols:
        Q1 = train_df[col].quantile(0.25)
        Q3 = train_df[col].quantile(0.75)
        IQR = Q3 - Q1
        lower_bound = Q1 - 1.5 * IQR
        upper_bound = Q3 + 1.5 * IQR
        outliers = train_df[(train_df[col] < lower_bound) | (train_df[col] > upper_bound)][col]

        outlier_summary.append({
            'Feature': col,
            'Outlier Count': len(outliers),
            'Lower Bound': round(lower_bound, 2),
            'Upper Bound': round(upper_bound, 2),
            'Min Value': round(train_df[col].min(), 2),
            'Max Value': round(train_df[col].max(), 2)
        })

    # Convert to DataFrame
    outlier_df = pd.DataFrame(outlier_summary)

    # Sort by outlier count (descending)
    outlier_df = outlier_df.sort_values(by='Outlier Count', ascending=False)

    # Display
    print("\n Outlier Analysis (IQR Method):")
    print(outlier_df.to_string(index=False))

In [ ]:
numerical_cols, categorical_cols = summarize_column_types(train_df)
analyze_outliers_iqr(train_df, numerical_cols)

 Dataset Column Type Summary 
Total Numerical Columns: 6
Numerical Columns:
   Age
   RoomService
   FoodCourt
   ShoppingMall
   Spa
   VRDeck

Total Categorical Columns: 8
Categorical Columns:
   PassengerId
   HomePlanet
   CryoSleep
   Cabin
   Destination
   VIP
   Name
   Transported

 Outlier Analysis (IQR Method):
     Feature  Outlier Count  Lower Bound  Upper Bound  Min Value  Max Value
 RoomService           1861        -70.5        117.5        0.0    14327.0
ShoppingMall           1829        -40.5         67.5        0.0    23492.0
   FoodCourt           1823       -114.0        190.0        0.0    29813.0
      VRDeck           1809        -69.0        115.0        0.0    24133.0
         Spa           1788        -88.5        147.5        0.0    22408.0
         Age             77         -9.5         66.5        0.0       79.0


In [ ]:
def plot_numerical_distributions(train_df, exclude_cols=None):
    """
    Plot histogram distributions for numerical columns in a DataFrame using subplots.

    Args:
        train_df (pandas.DataFrame): Input DataFrame to analyze.
        exclude_cols (list, optional): List of columns to exclude (e.g., ['PassengerId']). Defaults to None.

    Returns:
        None: Displays Plotly figures for each numerical column's distribution.
    """
    # Get numerical columns
    numerical_cols = train_df.select_dtypes(include=np.number).columns.tolist()

    # Exclude specified columns
    if exclude_cols:
        numerical_cols = [col for col in numerical_cols if col not in exclude_cols]

    # Create subplots
    fig = make_subplots(rows=len(numerical_cols), cols=1, subplot_titles=numerical_cols)

    # Use Plotly qualitative colors, extend with random colours
    colors = px.colors.qualitative.Plotly

    for i, col in enumerate(numerical_cols):
        # Histogram
        fig.add_trace(go.Histogram(
            x=train_df[col].dropna(),
            name=col,
            marker_color=colors[i % len(colors)]
        ), row=i + 1, col=1)

    # Update layout
    fig.update_layout(
        title_text='Distribution of Numerical Features',
        height=200 * len(numerical_cols),
        showlegend=False
    )

    fig.show()

In [ ]:
plot_numerical_distributions(train_df, exclude_cols=None)

In [ ]:
def visualize_outliers(train_df, numerical_cols):
    """
    Creating box plots for numerical features to visualize outliers using Plotly.

    Args:
        train_df (pd.DataFrame): The input DataFrame.
        numerical_cols (list): List of numerical column names.

    Returns:
        None: Displays box plots in subplots.
    """
    num_features = len(numerical_cols)
    rows = (num_features - 1) // 3 + 1  # max 3 plots per row

    # Use Plotly qualitative color palette and extend if needed
    base_colors = px.colors.qualitative.Plotly
    # If more features than colors, cycle through the palette
    colors = [base_colors[i % len(base_colors)] for i in range(num_features)]

    fig = make_subplots(
        rows=rows,
        cols=3,
        subplot_titles=[f'{col} Box Plot' for col in numerical_cols]
    )

    for i, (col, color) in enumerate(zip(numerical_cols, colors), 1):
        fig.add_trace(
            go.Box(
                y=train_df[col],
                name=col,
                boxpoints="outliers",
                marker_color=color
            ),
            row=(i - 1) // 3 + 1,
            col=(i - 1) % 3 + 1
        )

    fig.update_layout(
        height=300 * rows,
        title='Box Plots for Numerical Features (Outlier Detection)',
        showlegend=False
    )

    fig.show()


In [ ]:
numerical_cols = train_df.select_dtypes(include=['float64', 'int64']).columns.tolist()
visualize_outliers(train_df, numerical_cols)


In [ ]:
def analyze_key_features(train_df):
    """
    Perform EDA visualizations on key features:
    PassengerId groups 0001_01, HomePlanet, CryoSleep, Cabin (Deck & Side), Destination, and VIP.

    Args:
        train_df (pd.DataFrame): The training dataset.

    Returns:
        None: Displays interactive Plotly charts.
    """
    # Use Plotly qualitative palette for variety
    colors = px.colors.qualitative.D3
    color_cycle = cycle(colors)

    # 1. PassengerId group size distribution (0001   _    02)
    print("\nPassengerId Analysis:")
    train_df['Group'] = train_df['PassengerId'].str.split('_').str[0]
    group_counts = train_df['Group'].value_counts()
    group_sizes = group_counts.value_counts().sort_index()

    fig1 = px.bar(
        x=group_sizes.index,
        y=group_sizes.values,
        labels={'x': 'Group Size', 'y': 'Count'},
        title='Distribution of Group Sizes from PassengerId',
        color_discrete_sequence=[next(color_cycle)]
    )
    fig1.show()

    # 2. HomePlanet vs Transported
    print("\nHomePlanet Analysis:")
    fig2 = px.histogram(
        train_df,
        x='HomePlanet',
        color='Transported',
        barmode='group',
        title='HomePlanet vs Transported',
        color_discrete_sequence=[next(color_cycle), next(color_cycle)]
    )
    fig2.update_layout(xaxis_title='HomePlanet', yaxis_title='Count')
    fig2.show()

    # 3. CryoSleep vs Transported
    print("\nCryoSleep Analysis:")
    fig3 = px.histogram(
        train_df,
        x='CryoSleep',
        color='Transported',
        barmode='group',
        title='CryoSleep vs Transported',
        color_discrete_sequence=[next(color_cycle), next(color_cycle)]
    )
    fig3.update_layout(xaxis_title='CryoSleep', yaxis_title='Count')
    fig3.show()

    # 4. Cabin Analysis (Deck & Side) cabin-----> a/0/s , B/1/p
    print("\nCabin Analysis:")
    train_df['Deck'] = train_df['Cabin'].str.split('/').str[0].fillna('Unknown')
    train_df['Side'] = train_df['Cabin'].str.split('/').str[2].fillna('Unknown')

    fig4 = make_subplots(rows=1, cols=2, subplot_titles=('Deck vs Transported', 'Side vs Transported'))

    deck_color_1 = next(color_cycle)
    deck_color_2 = next(color_cycle)
    side_color_1 = next(color_cycle)
    side_color_2 = next(color_cycle)

    fig4.add_trace(go.Histogram(
        x=train_df[train_df['Transported'] == True]['Deck'],
        name='Transported (Deck)',
        opacity=0.6,
        marker_color=deck_color_1
    ), row=1, col=1)

    fig4.add_trace(go.Histogram(
        x=train_df[train_df['Transported'] == False]['Deck'],
        name='Not Transported (Deck)',
        opacity=0.6,
        marker_color=deck_color_2
    ), row=1, col=1)

    fig4.add_trace(go.Histogram(
        x=train_df[train_df['Transported'] == True]['Side'],
        name='Transported (Side)',
        opacity=0.6,
        marker_color=side_color_1
    ), row=1, col=2)

    fig4.add_trace(go.Histogram(
        x=train_df[train_df['Transported'] == False]['Side'],
        name='Not Transported (Side)',
        opacity=0.6,
        marker_color=side_color_2
    ), row=1, col=2)

    fig4.update_layout(
        barmode='overlay',
        title='Cabin Features: Deck and Side vs Transported',
        showlegend=True
    )
    fig4.show()

    # 5. Destination vs Transported
    print("\nDestination Analysis:")
    fig5 = px.histogram(
        train_df,
        x='Destination',
        color='Transported',
        barmode='group',
        title='Destination vs Transported',
        color_discrete_sequence=[next(color_cycle), next(color_cycle)]
    )
    fig5.update_layout(xaxis_title='Destination', yaxis_title='Count')
    fig5.show()

    # 6. VIP vs Transported
    print("\nVIP Analysis:")
    fig6 = px.histogram(
        train_df,
        x='VIP',
        color='Transported',
        barmode='group',
        title='VIP vs Transported',
        color_discrete_sequence=[next(color_cycle), next(color_cycle)]
    )
    fig6.update_layout(xaxis_title='VIP', yaxis_title='Count')
    fig6.show()

In [ ]:
analyze_key_features(train_df)



PassengerId Analysis:



HomePlanet Analysis:



CryoSleep Analysis:



Cabin Analysis:



Destination Analysis:



VIP Analysis:


# Correlation Heatmap

In [ ]:
def correlation_heatmap(train_df, numerical_cols, target_col='Transported'):
    """
    Plot an interactive correlation heatmap including numerical features and the target variable.

    Args:
        train_df (pd.DataFrame): The training dataset.
        numerical_cols (list): List of numerical column names.
        target_col (str): Name of the target column. Default is 'Transported'.

    Returns:
        None: Displays an interactive Plotly heatmap.
    """
    # Ensure target_col is included
    cols_to_corr = numerical_cols.copy()
    if target_col not in cols_to_corr:
        cols_to_corr.append(target_col)

    # Compute correlation matrix
    corr_matrix = train_df[cols_to_corr].corr()

    # Plot heatmap
    fig = px.imshow(
        corr_matrix,
        text_auto='.2f',
        color_continuous_scale='RdBu_r',
        title=f'Correlation Heatmap of Numerical Features including {target_col}'
    )

    fig.update_layout(
        xaxis_title="Features",
        yaxis_title="Features",
        width=800,
        height=700
    )

    fig.show()


In [ ]:
numerical_cols = train_df.select_dtypes(include=['float64', 'int64']).columns.tolist()
correlation_heatmap(train_df, numerical_cols)


# Data Cleaning and Imputation



In [ ]:
# Calculate number of rows after dropping nulls for train and test
train_rows_after_drop = train_df.dropna().shape[0]
test_rows_after_drop = test_df.dropna().shape[0]

# Calculate the percentage of rows dropped
train_percentage_dropped = 100 * (train_df.shape[0] - train_rows_after_drop) / train_df.shape[0]
test_percentage_dropped = 100 * (test_df.shape[0] - test_rows_after_drop) / test_df.shape[0]


print("Impact analysis of dropping missing values from the training and test datasets:")
print(f"Train dataset: Original rows: {train_df.shape[0]}, Rows after dropping nulls: {train_rows_after_drop}, Percentage of rows dropped: {train_percentage_dropped:.2f}%")
print(f"Test dataset: Original rows: {test_df.shape[0]}, Rows after dropping nulls: {test_rows_after_drop}, Percentage of rows dropped: {test_percentage_dropped:.2f}%")

Impact analysis of dropping missing values from the training and test datasets:
Train dataset: Original rows: 8693, Rows after dropping nulls: 6606, Percentage of rows dropped: 24.01%
Test dataset: Original rows: 4277, Rows after dropping nulls: 3281, Percentage of rows dropped: 23.29%


**The training and test datasets consist of 8,693 and 4,277 rows respectively. However, removing all rows with missing values would reduce the datasets to 6,606 and 3,281 rows resulting in a loss of approximately 24% of the data. Such a significant reduction could negatively impact model performance and generalization. Therefore, instead of dropping missing data, it is advisable to implement appropriate imputation techniques during the preprocessing stage to preserve data integrity and improve model robustness.**

In [ ]:
df_cleaned = train_df.copy()
print(" Original dataset copied for cleaning training set.\n")


 Original dataset copied for cleaning training set.



In [ ]:
df_cleaned_test = test_df.copy()
print(" Original dataset copied for cleaning test set.\n")

 Original dataset copied for cleaning test set.



# Imputing Missing Values - Numerical Columns

In [ ]:
def impute_numerical_median(df_train, df_test, numerical_cols):
    """
    Imputes missing values in numerical columns with their respective median values,
    computed independently for training and test DataFrames.

    Args:
        df_train (pd.DataFrame): Training DataFrame.
        df_test (pd.DataFrame): Test DataFrame.
        numerical_cols (list): List of numerical column names to impute.

    Returns:
        None: Imputation is done in-place for both DataFrames.
    """

    print("Imputing missing values in TRAINING set with its own medians:\n")
    for col in numerical_cols:
        median_train = df_train[col].median()
        df_train[col].fillna(median_train, inplace=True)
        print(f"  {col}: Train median = {median_train}")

    print("\nImputing missing values in TEST set with its own medians:\n")
    for col in numerical_cols:
        median_test = df_test[col].median()
        df_test[col].fillna(median_test, inplace=True)
        print(f"  {col}: Test median = {median_test}")

    print("\n All specified numerical columns have been imputed successfully in both sets.\n")


In [ ]:
numerical_cols = ['Age', 'RoomService', 'FoodCourt', 'ShoppingMall', 'Spa', 'VRDeck']
impute_numerical_median(df_cleaned, df_cleaned_test, numerical_cols)


Imputing missing values in TRAINING set with its own medians:

  Age: Train median = 27.0
  RoomService: Train median = 0.0
  FoodCourt: Train median = 0.0
  ShoppingMall: Train median = 0.0
  Spa: Train median = 0.0
  VRDeck: Train median = 0.0

Imputing missing values in TEST set with its own medians:

  Age: Test median = 26.0
  RoomService: Test median = 0.0
  FoodCourt: Test median = 0.0
  ShoppingMall: Test median = 0.0
  Spa: Test median = 0.0
  VRDeck: Test median = 0.0

 All specified numerical columns have been imputed successfully in both sets.



# Imputing Missing Values - Categorical Columns

In [ ]:
def impute_categorical_missing(df_train, df_test, categorical_cols):
    """
    Imputes missing values in categorical columns separately for train and test datasets.
    For 'Name', missing values are filled with 'Unknown'.
    For other columns, missing values are filled with the mode from their own DataFrame.

    Args:
        df_train (pd.DataFrame): Training DataFrame.
        df_test (pd.DataFrame): Test DataFrame.
        categorical_cols (list): List of categorical column names to impute.

    Returns:
        None: Imputation is done in-place for both DataFrames.
    """

    print("Imputing missing values in TRAINING set:\n")
    for col in categorical_cols:
        if col == 'Name':
            df_train[col].fillna('Unknown', inplace=True)
            print(f"  '{col}' (Train): filled with 'Unknown'")
        else:
            mode_train = df_train[col].mode()[0]
            df_train[col].fillna(mode_train, inplace=True)
            print(f"  '{col}' (Train): filled with mode = '{mode_train}'")

    print("\nImputing missing values in TEST set:\n")
    for col in categorical_cols:
        if col == 'Name':
            df_test[col].fillna('Unknown', inplace=True)
            print(f"  '{col}' (Test): filled with 'Unknown'")
        else:
            mode_test = df_test[col].mode()[0]
            df_test[col].fillna(mode_test, inplace=True)
            print(f"  '{col}' (Test): filled with mode = '{mode_test}'")

    print("\n All specified categorical columns have been imputed successfully in both sets.\n")


In [ ]:
categorical_cols = ['HomePlanet', 'CryoSleep', 'Cabin', 'Destination', 'VIP', 'Name']
impute_categorical_missing(df_cleaned, df_cleaned_test, categorical_cols)


Imputing missing values in TRAINING set:

  'HomePlanet' (Train): filled with mode = 'Earth'
  'CryoSleep' (Train): filled with mode = 'False'
  'Cabin' (Train): filled with mode = 'G/734/S'
  'Destination' (Train): filled with mode = 'TRAPPIST-1e'
  'VIP' (Train): filled with mode = 'False'
  'Name' (Train): filled with 'Unknown'

Imputing missing values in TEST set:

  'HomePlanet' (Test): filled with mode = 'Earth'
  'CryoSleep' (Test): filled with mode = 'False'
  'Cabin' (Test): filled with mode = 'G/160/P'
  'Destination' (Test): filled with mode = 'TRAPPIST-1e'
  'VIP' (Test): filled with mode = 'False'
  'Name' (Test): filled with 'Unknown'

 All specified categorical columns have been imputed successfully in both sets.



#  Split Cabin into Deck, Number, and Side & Impute missing cabin components with mode

In [ ]:
def split_and_impute_cabin(df_train, df_test):
    """
    Splits the 'Cabin' column into 'Deck', 'Number', and 'Side' columns,
    then imputes missing values in each column separately for train and test datasets using their own mode.

    Args:
        df_train (pd.DataFrame): Training DataFrame.
        df_test (pd.DataFrame): Test DataFrame.

    Returns:
        None: Modifies both DataFrames inplace.
    """
    print("Splitting 'Cabin' column in TRAINING set...\n")
    df_train[['Deck', 'Number', 'Side']] = df_train['Cabin'].str.split('/', expand=True)

    for col in ['Deck', 'Number', 'Side']:
        mode_train = df_train[col].mode()[0]
        df_train[col].fillna(mode_train, inplace=True)
        print(f" '{col}' (Train): Filled missing values with mode = '{mode_train}'")

    print("\nSplitting 'Cabin' column in TEST set...\n")
    df_test[['Deck', 'Number', 'Side']] = df_test['Cabin'].str.split('/', expand=True)

    for col in ['Deck', 'Number', 'Side']:
        mode_test = df_test[col].mode()[0]
        df_test[col].fillna(mode_test, inplace=True)
        print(f" '{col}' (Test): Filled missing values with mode = '{mode_test}'")

    print("\n 'Cabin' has been split and imputed in both train and test sets.\n")


In [ ]:
split_and_impute_cabin(df_cleaned, df_cleaned_test)


Splitting 'Cabin' column in TRAINING set...

 'Deck' (Train): Filled missing values with mode = 'F'
 'Number' (Train): Filled missing values with mode = '734'
 'Side' (Train): Filled missing values with mode = 'S'

Splitting 'Cabin' column in TEST set...

 'Deck' (Test): Filled missing values with mode = 'F'
 'Number' (Test): Filled missing values with mode = '160'
 'Side' (Test): Filled missing values with mode = 'P'

 'Cabin' has been split and imputed in both train and test sets.



In [ ]:
df_cleaned.columns

Index(['PassengerId', 'HomePlanet', 'CryoSleep', 'Cabin', 'Destination', 'Age',
       'VIP', 'RoomService', 'FoodCourt', 'ShoppingMall', 'Spa', 'VRDeck',
       'Name', 'Transported', 'Deck', 'Number', 'Side'],
      dtype='object')

**Group Features from PassengerId**





Features Created: GroupId, GroupSize, IsSolo, PersonNumber.

 Capture group dynamics, as passengers traveling together may have correlated Transported outcomes.



- The bar plot shows the proportion of passengers transported for each group size. Larger groups may have higher or lower transport rates, indicating social influence on outcomes.

In [ ]:
def feature_engineering(df_train, df_test):
    """
    Perform feature engineering separately for train and test datasets:
     Extract GroupId and PersonNumber from PassengerId
     Compute GroupSize and IsSolo flag
     Create Total_Spending and spending type categories
     Create no spending flag
     Create Age_Group bins

    Args:
        df_train (pd.DataFrame): Training DataFrame.
        df_test (pd.DataFrame): Test DataFrame.

    Returns:
        None: Modifies both DataFrames inplace.
    """

    def engineer(df, name="Dataset"):
        print(f"\n Feature engineering on {name}:")

        # Extract GroupId and PersonNumber
        df['GroupId'] = df['PassengerId'].apply(lambda x: x.split('_')[0])
        df['PersonNumber'] = df['PassengerId'].apply(lambda x: int(x.split('_')[1]))

        # Compute GroupSize
        df['GroupSize'] = df.groupby('GroupId')['GroupId'].transform('count')

        # Create IsSolo
        df['IsSolo'] = (df['GroupSize'] == 1).astype(int)

        # Total spending
        print("Creating 'Total_Spending' feature")
        spending_cols = ['RoomService', 'FoodCourt', 'ShoppingMall', 'Spa', 'VRDeck']
        df['Total_Spending'] = df[spending_cols].sum(axis=1)

        # No spending flag
        df['no spending'] = (df['Total_Spending'] == 0).astype(int)

        # Spending categories
        def categorize_spending(total):
            if total == 0:
                return 'No Expense'
            elif 1 <= total <= 716:
                return 'Low Expense'
            elif 717 <= total <= 1441:
                return 'Medium Expense'
            else:
                return 'High Expense'

        df['spending type'] = df['Total_Spending'].apply(categorize_spending)

        print(f"  Mean Total Spending: {df['Total_Spending'].mean():.2f}")
        print(f"  Median Total Spending: {df['Total_Spending'].median():.2f}")

         # Age Grouping into 4 categories
        bins = [0, 13, 22, 52, 80]
        labels = ['Children', 'Teen', 'Adult', 'Senior']
        df['Age_Group'] = pd.cut(df['Age'], bins=bins, labels=labels, right=False)


        print(" Feature engineering completed.\n")

    # Apply on both datasets
    engineer(df_train, "TRAIN set")
    engineer(df_test, "TEST set")


In [ ]:
feature_engineering(df_cleaned, df_cleaned_test)



 Feature engineering on TRAIN set:
Creating 'Total_Spending' feature
  Mean Total Spending: 1440.87
  Median Total Spending: 716.00
 Feature engineering completed.


 Feature engineering on TEST set:
Creating 'Total_Spending' feature
  Mean Total Spending: 1417.68
  Median Total Spending: 714.00
 Feature engineering completed.



In [ ]:
df_cleaned.head()

PassengerId HomePlanet  CryoSleep  Cabin  Destination   Age    VIP  \
0     0001_01     Europa      False  B/0/P  TRAPPIST-1e  39.0  False   
1     0002_01      Earth      False  F/0/S  TRAPPIST-1e  24.0  False   
2     0003_01     Europa      False  A/0/S  TRAPPIST-1e  58.0   True   
3     0003_02     Europa      False  A/0/S  TRAPPIST-1e  33.0  False   
4     0004_01      Earth      False  F/1/S  TRAPPIST-1e  16.0  False   

   RoomService  FoodCourt  ShoppingMall  ...  Number  Side GroupId  \
0          0.0        0.0           0.0  ...       0     P    0001   
1        109.0        9.0          25.0  ...       0     S    0002   
2         43.0     3576.0           0.0  ...       0     S    0003   
3          0.0     1283.0         371.0  ...       0     S    0003   
4        303.0       70.0         151.0  ...       1     S    0004   

   PersonNumber GroupSize IsSolo Total_Spending no spending   spending type  \
0             1         1      1            0.0           1      No Expense   
1             1         1      1          736.0           0  Medium Expense   
2             1         2      0        10383.0           0    High Expense   
3             2         2      0         5176.0           0    High Expense   
4             1         1      1         1091.0           0  Medium Expense   

   Age_Group  
0      Adult  
1      Adult  
2     Senior  
3      Adult  
4       Teen  

[5 rows x 25 columns]

In [ ]:
def check_missing_values(df_train, df_test):
    print("Final check for missing values in TRAIN set:\n")
    missing_train = df_train.isnull().sum()
    missing_train = missing_train[missing_train > 0]

    if missing_train.empty:
        print("  All missing values successfully handled in TRAIN set!\n")
    else:
        print("  Missing values still present in TRAIN set:\n", missing_train, "\n")

    print("Final check for missing values in TEST set:\n")
    missing_test = df_test.isnull().sum()
    missing_test = missing_test[missing_test > 0]

    if missing_test.empty:
        print("  All missing values successfully handled in TEST set!\n")
    else:
        print("  Missing values still present in TEST set:\n", missing_test, "\n")


In [ ]:
check_missing_values(df_cleaned, df_cleaned_test)


Final check for missing values in TRAIN set:

  All missing values successfully handled in TRAIN set!

Final check for missing values in TEST set:

  All missing values successfully handled in TEST set!



# In-Depth EDA ( for Cleaned data)

In [ ]:
def perform_eda(df, target, numerical_cols, categorical_cols, group_col=None, deck_col=None):
    """
    Perform EDA with Plotly:
     Univariate (Histogram + Boxplot for numerical)
     Numerical vs Target (Boxplot + Violin)
     Categorical vs Target (Bar Count)
     Grouped summary by group_col (e.g., GroupSize)
     Deck analysis from Cabin feature (if deck_col provided)
    """
    color_palette = px.colors.qualitative.Bold
    color_cycle = cycle(color_palette)

    def apply_white_bg(fig):
        fig.update_layout(
            plot_bgcolor='white',
            paper_bgcolor='white',
            font_color='black',
            title_font_color='black',
            legend_title_font_color='black',
            legend_bgcolor='white',
            xaxis=dict(showgrid=True, gridcolor='lightgrey'),
            yaxis=dict(showgrid=True, gridcolor='lightgrey')
        )

    # Univariate: Histogram + Boxplot
    for col in numerical_cols:
        fig = make_subplots(rows=1, cols=2, subplot_titles=(f"Histogram of {col}", f"Boxplot of {col}"))

        hist = px.histogram(df, x=col, color_discrete_sequence=[next(color_cycle)])
        for trace in hist.data:
            fig.add_trace(trace, row=1, col=1)

        box = px.box(df, y=col, color_discrete_sequence=[next(color_cycle)])
        for trace in box.data:
            fig.add_trace(trace, row=1, col=2)

        fig.update_layout(title_text=f"Univariate Analysis: {col}", width=1000, height=400, showlegend=False)
        apply_white_bg(fig)
        fig.show()

    # Numerical vs Target: Box + Violin
    for col in numerical_cols:
        fig = make_subplots(rows=1, cols=2,
                            subplot_titles=(f"{col} by {target} (Boxplot)", f"{col} by {target} (Violin)"))

        color_seq = [next(color_cycle) for _ in df[target].unique()]
        box = px.box(df, x=target, y=col, color=target, color_discrete_sequence=color_seq)
        for trace in box.data:
            fig.add_trace(trace, row=1, col=1)

        violin = px.violin(df, x=target, y=col, color=target, box=True, points="all", color_discrete_sequence=color_seq)
        for trace in violin.data:
            fig.add_trace(trace, row=1, col=2)

        fig.update_layout(title_text=f"{col} vs {target}", width=1000, height=450)
        apply_white_bg(fig)
        fig.show()

    # Categorical vs Target
    for col in categorical_cols:
        grouped = df.groupby([col, target]).size().reset_index(name='count')
        color_seq = [next(color_cycle) for _ in df[target].unique()]
        fig = px.bar(grouped, x=col, y='count', color=target, barmode='group', text='count',
                     title=f"{col} vs {target}", color_discrete_sequence=color_seq)
        fig.update_layout(xaxis_title=col, yaxis_title="Count", height=450)
        apply_white_bg(fig)
        fig.show()

    # Group Size vs Transported (optional)
    if group_col:
        group_data = df.groupby(group_col)[target].mean().reset_index()
        fig = px.bar(group_data, x=group_col, y=target,
                     title=f"Proportion of {target} by {group_col}",
                     labels={target: f"Proportion {target}", group_col: group_col},
                     color=target,
                     color_discrete_sequence=[next(color_cycle)])
        fig.update_layout(showlegend=False)
        apply_white_bg(fig)
        fig.show()

    # Deck analysis (optional)
    if deck_col and 'Cabin' in df.columns:
        deck_df = df[df['Cabin'].notna() & ~df['Cabin'].str.startswith('Unknown')].copy()
        deck_df[deck_col] = deck_df['Cabin'].str.split('/').str[0].fillna('Unknown')

        deck_summary = deck_df.groupby(deck_col)[target].mean().reset_index().sort_values(by=target, ascending=False)
        fig = px.bar(deck_summary, x=deck_col, y=target, text=target,
                     title=f"Proportion of {target} by {deck_col}",
                     color=target,
                     color_continuous_scale='Viridis')
        fig.update_traces(texttemplate='%{text:.2%}', textposition='outside')
        fig.update_layout(height=500, showlegend=False)
        apply_white_bg(fig)
        fig.show()


In [ ]:
numerical_cols = ['Age', 'RoomService', 'FoodCourt', 'ShoppingMall', 'Spa', 'VRDeck']
categorical_cols = ['HomePlanet', 'CryoSleep', 'Destination', 'VIP', 'Deck', 'Side', 'IsSolo', 'spending type', 'Age_Group']

perform_eda(df_cleaned,
            target='Transported',
            numerical_cols=numerical_cols,
            categorical_cols=categorical_cols,
            group_col='GroupSize',
            deck_col='Deck')


# Correlation Heatmap with Target variable

In [ ]:
df_cleaned.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 8693 entries, 0 to 8692
Data columns (total 26 columns):
 #   Column          Non-Null Count  Dtype   
---  ------          --------------  -----   
 0   PassengerId     8693 non-null   object  
 1   HomePlanet      8693 non-null   object  
 2   CryoSleep       8693 non-null   bool    
 3   Cabin           8693 non-null   object  
 4   Destination     8693 non-null   object  
 5   Age             8693 non-null   float64 
 6   VIP             8693 non-null   bool    
 7   RoomService     8693 non-null   float64 
 8   FoodCourt       8693 non-null   float64 
 9   ShoppingMall    8693 non-null   float64 
 10  Spa             8693 non-null   float64 
 11  VRDeck          8693 non-null   float64 
 12  Name            8693 non-null   object  
 13  Transported     8693 non-null   bool    
 14  Group           8693 non-null   object  
 15  Deck            8693 non-null   object  
 16  Side            8693 non-null   object  
 17  Number        

In [ ]:
df_cleaned_test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4277 entries, 0 to 4276
Data columns (total 24 columns):
 #   Column          Non-Null Count  Dtype   
---  ------          --------------  -----   
 0   PassengerId     4277 non-null   object  
 1   HomePlanet      4277 non-null   object  
 2   CryoSleep       4277 non-null   bool    
 3   Cabin           4277 non-null   object  
 4   Destination     4277 non-null   object  
 5   Age             4277 non-null   float64 
 6   VIP             4277 non-null   bool    
 7   RoomService     4277 non-null   float64 
 8   FoodCourt       4277 non-null   float64 
 9   ShoppingMall    4277 non-null   float64 
 10  Spa             4277 non-null   float64 
 11  VRDeck          4277 non-null   float64 
 12  Name            4277 non-null   object  
 13  Deck            4277 non-null   object  
 14  Number          4277 non-null   object  
 15  Side            4277 non-null   object  
 16  GroupId         4277 non-null   object  
 17  PersonNumber  

In [ ]:
def plot_correlation_heatmap(df, target_col=None, cols_to_include=None, title="Correlation Heatmap"):
    """
    Plot an interactive correlation heatmap using Plotly.

    Parameters:
     df: pandas DataFrame
     target_col: (optional) column to include in correlation, like 'Transported'
     cols_to_include: (optional) list of specific columns to include
     title: (str) Title for the heatmap
    """
    # If boolean target, convert to int
    if target_col and df[target_col].dtype == bool:
        df[target_col] = df[target_col].astype(int)

    # Select columns
    if cols_to_include:
        data = df[cols_to_include].copy()
    else:
        data = df.select_dtypes(include='number').copy()  # Only numeric cols

    # Compute correlation
    corr_matrix = data.corr().round(2)

    # Convert to long format for Plotly
    corr_long = corr_matrix.reset_index().melt(id_vars='index')
    corr_long.columns = ['Feature1', 'Feature2', 'Correlation']

    # Plot heatmap
    fig = px.imshow(
        corr_matrix,
        text_auto=True,
        color_continuous_scale='RdBu_r',
        zmin=-1, zmax=1,
        title=title,
        labels=dict(x="Feature", y="Feature", color="Correlation")
    )
    fig.update_layout(width=700, height=600)
    fig.show()


In [ ]:
cols_to_include = [
    'Age', 'RoomService', 'FoodCourt', 'ShoppingMall',
    'Spa', 'VRDeck', 'Total_Spending', 'PersonNumber',
    'GroupSize', 'IsSolo', 'no spending', 'Transported'
]

plot_correlation_heatmap(df=df_cleaned, target_col='Transported', cols_to_include=cols_to_include)


# One-Hot Encoding Categorical Features & scaling

Prepares categorical features for modeling, as most algorithms (except catboost) require numerical inputs.

Transforms these columns into numerical values using one hot Encoder.

HomePlanet, Destination, Deck, Side, AgeGroup, Surname

## Models training and evaluation

In [ ]:
def run_model_pipeline(df, target_col, numerical_cols, categorical_cols):
    X = df.drop(columns=[target_col])
    y = df[target_col]

    X_train, X_test, y_train, y_test = train_test_split(
        X, y, test_size=0.2, stratify=y, random_state=99
    )

    numeric_transformer = Pipeline(steps=[
        ('imputer', SimpleImputer(strategy='median')),
        ('scaler', StandardScaler())
    ])

    categorical_transformer = Pipeline(steps=[
        ('imputer', SimpleImputer(strategy='most_frequent')),
        ('encoder', OneHotEncoder(handle_unknown='ignore', sparse_output=False))
    ])

    preprocessor = ColumnTransformer(transformers=[
        ('num', numeric_transformer, numerical_cols),
        ('cat', categorical_transformer, categorical_cols)
    ])

    models = {
        'Logistic Regression': LogisticRegression(max_iter=1000),
        'SVM': SVC(probability=True),
        'Random Forest': RandomForestClassifier(random_state=99),
        'XGBoost': XGBClassifier(use_label_encoder=False, eval_metric='logloss'),
        'CatBoost': CatBoostClassifier(verbose=0)
    }

    results = {}
    accuracy_scores = {}

    for name, model in models.items():
        pipe = Pipeline(steps=[
            ('preprocessor', preprocessor),
            ('classifier', model)
        ])

        print(f"\n Training: {name}")
        pipe.fit(X_train, y_train)
        y_pred = pipe.predict(X_test)
        y_proba = pipe.predict_proba(X_test)[:, 1]

        acc = accuracy_score(y_test, y_pred)
        accuracy_scores[name] = acc

        print(f" Accuracy: {acc:.4f}")
        print(" Classification Report:\n", classification_report(y_test, y_pred))
        print(" Confusion Matrix:\n", confusion_matrix(y_test, y_pred))
        print("---------------------------------------------------------\n")

        # Confusion Matrix Plot (Plotly)
        cm = confusion_matrix(y_test, y_pred)
        labels = [str(c) for c in np.unique(y)]
        fig_cm = go.Figure(data=go.Heatmap(
            z=cm,
            x=labels,
            y=labels,
            colorscale='Blues',
            text=cm,
            texttemplate="%{text}",
            showscale=True,
        ))
        fig_cm.update_layout(
            title=f"{name} - Confusion Matrix",
            xaxis_title="Predicted Label",
            yaxis_title="True Label"
        )
        fig_cm.show()

        # ROC Curve Plot (Plotly)
        fpr, tpr, _ = roc_curve(y_test, y_proba)
        auc_score = roc_auc_score(y_test, y_proba)
        fig_roc = go.Figure()
        fig_roc.add_trace(go.Scatter(x=fpr, y=tpr, mode='lines', name=f'ROC curve (AUC = {auc_score:.2f})'))
        fig_roc.add_trace(go.Scatter(x=[0, 1], y=[0, 1], mode='lines', line=dict(dash='dash'), name='Random Guess'))
        fig_roc.update_layout(
            title=f"{name} - ROC Curve",
            xaxis_title='False Positive Rate',
            yaxis_title='True Positive Rate',
            xaxis=dict(range=[0, 1]),
            yaxis=dict(range=[0, 1]),
            template='plotly_white'
        )
        fig_roc.show()

        # Precision-Recall Curve Plot
        precision, recall, _ = precision_recall_curve(y_test, y_proba)
        fig_pr = go.Figure()
        fig_pr.add_trace(go.Scatter(x=recall, y=precision, mode='lines', name='Precision-Recall curve'))
        fig_pr.update_layout(
            title=f"{name} - Precision-Recall Curve",
            xaxis_title='Recall',
            yaxis_title='Precision',
            template='plotly_white'
        )
        fig_pr.show()

        # Feature Importances (Tree-based only)
        if hasattr(model, "feature_importances_"):
            encoded_feature_names = preprocessor.named_transformers_['cat']['encoder'].get_feature_names_out(categorical_cols)
            all_features = np.concatenate([numerical_cols, encoded_feature_names])
            importances = model.feature_importances_

            top_features = pd.Series(importances, index=all_features).sort_values(ascending=False)[:15]
            fig = px.bar(top_features, title=f"{name} - Top Feature Importances",
                         labels={"value": "Importance", "index": "Feature"})
            fig.show()

        results[name] = {
            'model': pipe,
            'accuracy': acc,
            'confusion_matrix': cm,
            'report': classification_report(y_test, y_pred, output_dict=True),
            'roc_auc': roc_auc_score(y_test, y_proba)
        }

    # Compare model accuracies
    acc_df = pd.DataFrame.from_dict(accuracy_scores, orient='index', columns=['Accuracy']).sort_values(by='Accuracy', ascending=False)
    fig_acc = px.bar(acc_df, x=acc_df.index, y='Accuracy', text='Accuracy',
                 title=' Model Accuracy Comparison',
                 labels={'index': 'Model', 'Accuracy': 'Accuracy'},
                 color='Accuracy', color_continuous_scale='Blues')
    fig_acc.update_traces(texttemplate='%{text:.4f}', textposition='outside')
    fig_acc.update_layout(uniformtext_minsize=8, uniformtext_mode='hide')
    fig_acc.show()

    return results


## Hyperparameter Tuning Pipeline for All Models

In [ ]:
from sklearn.model_selection import GridSearchCV, RandomizedSearchCV

def tune_models_pipeline( df, target_col, numerical_cols, categorical_cols, search_type='random', n_iter=10, cv=3
):
    """
    Performs hyperparameter tuning for multiple models with preprocessing pipeline.

    Parameters:
        df (pd.DataFrame): Input DataFrame.
        target_col (str): Target column name.
        numerical_cols (list): List of numerical feature names.
        categorical_cols (list): List of categorical feature names.
        search_type (str): 'grid' or 'random' for GridSearchCV or RandomizedSearchCV.
        n_iter (int): Number of iterations for random search.
        cv (int): Cross-validation folds.

    Returns:
        dict: Best models and their performance.
    """

    X = df.drop(columns=[target_col])
    y = df[target_col]

    X_train, X_test, y_train, y_test = train_test_split(
        X, y, test_size=0.2, stratify=y, random_state=99
    )

    # Preprocessing
    numeric_transformer = Pipeline([
        ('imputer', SimpleImputer(strategy='median')),
        ('scaler', StandardScaler())
    ])
    categorical_transformer = Pipeline([
        ('imputer', SimpleImputer(strategy='most_frequent')),
        ('encoder', OneHotEncoder(handle_unknown='ignore', sparse_output=False))
    ])
    preprocessor = ColumnTransformer([
        ('num', numeric_transformer, numerical_cols),
        ('cat', categorical_transformer, categorical_cols)
    ])

    # Model search space
    param_grids = {
        'Logistic Regression': {
            'classifier__C': [0.01, 0.1, 1, 10],
            'classifier__penalty': ['l2'],
            'classifier__solver': ['lbfgs']
        },
        'SVM': {
            'classifier__C': [0.1, 1, 10],
            'classifier__kernel': ['linear', 'rbf'],
            'classifier__gamma': ['scale', 'auto']
        },
        'Random Forest': {
            'classifier__n_estimators': [100, 200],
            'classifier__max_depth': [5, 10, None],
            'classifier__min_samples_split': [2, 5],
            'classifier__bootstrap': [True, False]
        },
        'XGBoost': {
            'classifier__n_estimators': [100, 200],
            'classifier__max_depth': [3, 6],
            'classifier__learning_rate': [0.01, 0.1, 0.2],
            'classifier__subsample': [0.8, 1]
        },
        'CatBoost': {
            'classifier__iterations': [100, 200],
            'classifier__learning_rate': [0.01, 0.1,0.3,0.5,0.6,0.7],
            'classifier__depth': [4, 6, 8,9,10]
        }
    }

    models = {
        'Logistic Regression': LogisticRegression(max_iter=1000),
        'SVM': SVC(probability=True),
        'Random Forest': RandomForestClassifier(random_state=99),
        'XGBoost': XGBClassifier(use_label_encoder=False, eval_metric='logloss'),
        'CatBoost': CatBoostClassifier(verbose=0)
    }

    best_results = {}

    for name, model in models.items():
        print(f"\n Tuning: {name}")
        pipe = Pipeline([
            ('preprocessor', preprocessor),
            ('classifier', model)
        ])

        param_grid = param_grids[name]

        if search_type == 'grid':
            search = GridSearchCV(pipe, param_grid, cv=cv, n_jobs=-1, scoring='accuracy', verbose=1)
        else:
            search = RandomizedSearchCV(pipe, param_grid, cv=cv, n_iter=n_iter, n_jobs=-1,
                                        scoring='accuracy', random_state=99, verbose=1)

        search.fit(X_train, y_train)
        best_model = search.best_estimator_
        y_pred = best_model.predict(X_test)
        y_proba = best_model.predict_proba(X_test)[:, 1]

        acc = accuracy_score(y_test, y_pred)
        auc = roc_auc_score(y_test, y_proba)

        print(f" Best Parameters: {search.best_params_}")
        print(f" Accuracy: {acc:.4f} | AUC: {auc:.4f}")

        best_results[name] = {
            'best_estimator': best_model,
            'best_params': search.best_params_,
            'accuracy': acc,
            'roc_auc': auc,
            'classification_report': classification_report(y_test, y_pred, output_dict=True)
        }

    return best_results, X_test, y_test



In [ ]:
best_models = tune_models_pipeline(
     df=df_cleaned,
    target_col='Transported',
     numerical_cols=numerical_cols,
     categorical_cols=categorical_cols,
     search_type='GridSearchCV',
     n_iter=10,
     cv=3
 )



 Tuning: Logistic Regression
Fitting 3 folds for each of 4 candidates, totalling 12 fits
 Best Parameters: {'classifier__solver': 'lbfgs', 'classifier__penalty': 'l2', 'classifier__C': 1}
 Accuracy: 0.7930 | AUC: 0.8752

 Tuning: SVM
Fitting 3 folds for each of 10 candidates, totalling 30 fits
 Best Parameters: {'classifier__kernel': 'rbf', 'classifier__gamma': 'scale', 'classifier__C': 10}
 Accuracy: 0.7959 | AUC: 0.8737

 Tuning: Random Forest
Fitting 3 folds for each of 10 candidates, totalling 30 fits
 Best Parameters: {'classifier__n_estimators': 200, 'classifier__min_samples_split': 5, 'classifier__max_depth': 10, 'classifier__bootstrap': False}
 Accuracy: 0.8028 | AUC: 0.8796

 Tuning: XGBoost
Fitting 3 folds for each of 10 candidates, totalling 30 fits
 Best Parameters: {'classifier__subsample': 0.8, 'classifier__n_estimators': 100, 'classifier__max_depth': 6, 'classifier__learning_rate': 0.1}
 Accuracy: 0.8022 | AUC: 0.8863

 Tuning: CatBoost
Fitting 3 folds for each of 10 ca

In [ ]:
def plot_model_metrics(best_models, baseline_results, X_test, y_test):
    import pandas as pd
    import plotly.express as px
    import plotly.graph_objects as go
    from sklearn.metrics import (
        roc_curve, precision_recall_curve,
        confusion_matrix
    )

    # For storing metric comparisons
    metrics_summary = []

    for name, info in best_models.items():
        # Tuned model
        tuned_model = info['best_estimator']
        y_pred = tuned_model.predict(X_test)
        y_proba = tuned_model.predict_proba(X_test)[:, 1]

        # Baseline accuracy
        baseline_acc = baseline_results[name]['accuracy']
        tuned_acc = info['accuracy']

        # Store comparison
        metrics_summary.append({
            'Model': name,
            'Before Tuning': baseline_acc,
            'After Tuning': tuned_acc
        })

        #  plot curves for each model

        # Confusion Matrix
        cm = confusion_matrix(y_test, y_pred)
        fig_cm = go.Figure(data=go.Heatmap(
            z=cm,
            x=['Pred 0', 'Pred 1'],
            y=['True 0', 'True 1'],
            colorscale='Blues',
            text=cm,
            texttemplate="%{text}",
            showscale=True
        ))
        fig_cm.update_layout(title=f"{name} - Confusion Matrix")
        fig_cm.show()

        # ROC Curve
        fpr, tpr, _ = roc_curve(y_test, y_proba)
        auc = info['roc_auc']
        fig_roc = go.Figure()
        fig_roc.add_trace(go.Scatter(x=fpr, y=tpr, mode='lines', name=f'{name} (AUC={auc:.3f})'))
        fig_roc.add_trace(go.Scatter(x=[0, 1], y=[0, 1], mode='lines', line=dict(dash='dash'), name='Random'))
        fig_roc.update_layout(
            title=f"{name} - ROC Curve",
            xaxis_title='False Positive Rate',
            yaxis_title='True Positive Rate',
            template='plotly_white'
        )
        fig_roc.show()

        # Precision-Recall Curve
        precision, recall, _ = precision_recall_curve(y_test, y_proba)
        fig_pr = go.Figure()
        fig_pr.add_trace(go.Scatter(x=recall, y=precision, mode='lines', name=name))
        fig_pr.update_layout(
            title=f"{name} - Precision-Recall Curve",
            xaxis_title='Recall',
            yaxis_title='Precision',
            template='plotly_white'
        )
        fig_pr.show()

    # Comparison Plot: Accuracy Before vs After Tuning
    df_metrics = pd.DataFrame(metrics_summary).melt(
        id_vars='Model', var_name='Stage', value_name='Accuracy'
    )
    fig_compare = px.bar(
        df_metrics,
        x='Model', y='Accuracy', color='Stage', barmode='group',
        text='Accuracy', title="Model Accuracy: Before vs After Hyperparameter Tuning"
    )
    fig_compare.update_traces(texttemplate='%{text:.3f}', textposition='outside')
    fig_compare.update_layout(uniformtext_minsize=8, uniformtext_mode='hide')
    fig_compare.show()


In [ ]:
numerical_cols = ['Age', 'RoomService', 'FoodCourt', 'ShoppingMall', 'Spa', 'VRDeck', 'Total_Spending']
categorical_cols = ['HomePlanet', 'CryoSleep', 'Destination', 'VIP', 'Deck', 'Side', 'IsSolo', 'GroupSize']

baseline_results = run_model_pipeline(df_cleaned, 'Transported', numerical_cols=numerical_cols, categorical_cols=categorical_cols)
tuned_results, X_test, y_test = tune_models_pipeline(df_cleaned, 'Transported', numerical_cols=numerical_cols, categorical_cols=categorical_cols)

plot_model_metrics(tuned_results, baseline_results, X_test, y_test)



 Training: Logistic Regression
 Accuracy: 0.7867
 Classification Report:
               precision    recall  f1-score   support

           0       0.80      0.76      0.78       863
           1       0.78      0.81      0.79       876

    accuracy                           0.79      1739
   macro avg       0.79      0.79      0.79      1739
weighted avg       0.79      0.79      0.79      1739

 Confusion Matrix:
 [[657 206]
 [165 711]]
---------------------------------------------------------




 Training: SVM
 Accuracy: 0.7982
 Classification Report:
               precision    recall  f1-score   support

           0       0.80      0.79      0.79       863
           1       0.79      0.81      0.80       876

    accuracy                           0.80      1739
   macro avg       0.80      0.80      0.80      1739
weighted avg       0.80      0.80      0.80      1739

 Confusion Matrix:
 [[680 183]
 [168 708]]
---------------------------------------------------------




 Training: Random Forest
 Accuracy: 0.7826
 Classification Report:
               precision    recall  f1-score   support

           0       0.76      0.82      0.79       863
           1       0.81      0.74      0.77       876

    accuracy                           0.78      1739
   macro avg       0.78      0.78      0.78      1739
weighted avg       0.78      0.78      0.78      1739

 Confusion Matrix:
 [[711 152]
 [226 650]]
---------------------------------------------------------




 Training: XGBoost
 Accuracy: 0.8074
 Classification Report:
               precision    recall  f1-score   support

           0       0.81      0.79      0.80       863
           1       0.80      0.82      0.81       876

    accuracy                           0.81      1739
   macro avg       0.81      0.81      0.81      1739
weighted avg       0.81      0.81      0.81      1739

 Confusion Matrix:
 [[686 177]
 [158 718]]
---------------------------------------------------------




 Training: CatBoost
 Accuracy: 0.8097
 Classification Report:
               precision    recall  f1-score   support

           0       0.82      0.79      0.80       863
           1       0.80      0.83      0.81       876

    accuracy                           0.81      1739
   macro avg       0.81      0.81      0.81      1739
weighted avg       0.81      0.81      0.81      1739

 Confusion Matrix:
 [[680 183]
 [148 728]]
---------------------------------------------------------




 Tuning: Logistic Regression
Fitting 3 folds for each of 4 candidates, totalling 12 fits
 Best Parameters: {'classifier__solver': 'lbfgs', 'classifier__penalty': 'l2', 'classifier__C': 0.1}
 Accuracy: 0.7826 | AUC: 0.8724

 Tuning: SVM
Fitting 3 folds for each of 10 candidates, totalling 30 fits
 Best Parameters: {'classifier__kernel': 'rbf', 'classifier__gamma': 'scale', 'classifier__C': 10}
 Accuracy: 0.8028 | AUC: 0.8711

 Tuning: Random Forest
Fitting 3 folds for each of 10 candidates, totalling 30 fits
 Best Parameters: {'classifier__n_estimators': 100, 'classifier__min_samples_split': 2, 'classifier__max_depth': 10, 'classifier__bootstrap': False}
 Accuracy: 0.7999 | AUC: 0.8794

 Tuning: XGBoost
Fitting 3 folds for each of 10 candidates, totalling 30 fits
 Best Parameters: {'classifier__subsample': 1, 'classifier__n_estimators': 200, 'classifier__max_depth': 3, 'classifier__learning_rate': 0.2}
 Accuracy: 0.8114 | AUC: 0.8878

 Tuning: CatBoost
Fitting 3 folds for each of 10 ca

## Prediction on Unseen Test dataset and submission csv file for kaggle submission

In [ ]:
best_model = tuned_results['CatBoost']['best_estimator']
X_test_final = df_cleaned_test.copy()
test_preds = best_model.predict(X_test_final)
test_preds_bool = test_preds.astype(bool)


test_original = pd.read_csv("https://raw.githubusercontent.com/Titanic-minds-group-14/Kaggle-challenge-group-14-/refs/heads/main/Data/test.csv")

submission_df = pd.DataFrame({
    'PassengerId': test_original['PassengerId'],
    'Transported': test_preds_bool
})

# Save to CSV
submission_df.to_csv('submission_CatBoost1.csv', index=False)
print("Submission file created: submission_CatBoost.csv")
files.download('submission_CatBoost1.csv')

Submission file created: submission_CatBoost.csv


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

## XAI Techniques

In [ ]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from catboost import CatBoostClassifier
import shap
import plotly.express as px
import plotly.graph_objects as go
import json
from google.colab import files
import warnings
warnings.filterwarnings('ignore')

# Preprocessing function to derive features
def preprocess_data(df, is_train=False):
    df = df.copy()
    # Extract Deck and Side from Cabin
    df['Deck'] = df['Cabin'].str.split('/').str[0]
    df['Side'] = df['Cabin'].str.split('/').str[-1]
    # Calculate Total_Spending
    spending_cols = ['RoomService', 'FoodCourt', 'ShoppingMall', 'Spa', 'VRDeck']
    df['Total_Spending'] = df[spending_cols].sum(axis=1)
    # Extract Group and compute GroupSize
    df['Group'] = df['PassengerId'].str.split('_').str[0]
    df['GroupSize'] = df.groupby('Group')['PassengerId'].transform('count')
    # Create IsSolo feature
    df['IsSolo'] = (df['GroupSize'] == 1).astype(bool)
    # Keep only required columns
    columns_to_keep = ['PassengerId'] + numerical_cols + categorical_cols
    if is_train:
        columns_to_keep.append('Transported')

    # Ensure we only keep columns that exist in the dataframe
    columns_to_keep = [col for col in columns_to_keep if col in df.columns]

    return df[columns_to_keep]

# Function to train model, generate SHAP plots, and return model/preprocessor
def apply_shap_explanations(df, target_col, numerical_cols, categorical_cols, model_name='CatBoost'):
    X = df.drop(columns=[target_col, 'PassengerId'])
    y = df[target_col]
    X_train, X_test, y_train, y_test = train_test_split(
        X, y, test_size=0.2, stratify=y, random_state=99
    )
    # Define preprocessing pipeline
    numeric_transformer = Pipeline(steps=[
        ('imputer', SimpleImputer(strategy='median')),
        ('scaler', StandardScaler())
    ])
    categorical_transformer = Pipeline(steps=[
        ('imputer', SimpleImputer(strategy='most_frequent')),
        ('encoder', OneHotEncoder(handle_unknown='ignore', sparse_output=False))
    ])
    preprocessor = ColumnTransformer(transformers=[
        ('num', numeric_transformer, numerical_cols),
        ('cat', categorical_transformer, categorical_cols)
    ])
    # Define model
    model = CatBoostClassifier(verbose=0)
    pipe = Pipeline(steps=[
        ('preprocessor', preprocessor),
        ('classifier', model)
    ])
    # Fit the model
    pipe.fit(X_train, y_train)

    # Transform test data for SHAP analysis
    X_test_transformed = preprocessor.transform(X_test)

    # Compute SHAP values
    print(f"Computing SHAP values for {model_name}...")
    explainer = shap.TreeExplainer(pipe.named_steps['classifier'])
    shap_values = explainer.shap_values(X_test_transformed)

    # Get feature names after preprocessing
    feature_names = np.concatenate([
        numerical_cols,
        preprocessor.named_transformers_['cat']['encoder'].get_feature_names_out(categorical_cols)
    ])
    print(f"Number of features after preprocessing: {len(feature_names)}")
    print(f"Feature names: {feature_names.tolist()}")

    # Save SHAP values to JSON
    shap_dict = {
        'shap_values': shap_values.tolist(),
        'feature_names': feature_names.tolist()
    }
    with open(f'shap_values_{model_name.lower().replace(" ", "_")}.json', 'w') as f:
        json.dump(shap_dict, f)

    # SHAP Summary Plot (Bar)
    shap_summary = np.abs(shap_values).mean(axis=0)
    top_features = pd.Series(shap_summary, index=feature_names).sort_values(ascending=False)[:15]
    fig_shap_summary = px.bar(
        top_features,
        title=f"{model_name} - SHAP Feature Importance",
        labels={"value": "Mean SHAP Value", "index": "Feature"}
    )
    fig_shap_summary.show()

    # SHAP Dependence Plot for top feature
    top_feature = top_features.index[0]
    fig_shap_dep = go.Figure()
    fig_shap_dep.add_trace(go.Scatter(
        x=X_test_transformed[:, feature_names.tolist().index(top_feature)],
        y=shap_values[:, feature_names.tolist().index(top_feature)],
        mode='markers',
        marker=dict(color='blue', opacity=0.5)
    ))
    fig_shap_dep.update_layout(
        title=f"{model_name} - SHAP Dependence Plot for {top_feature}",
        xaxis_title=top_feature,
        yaxis_title="SHAP Value",
        template='plotly_white'
    )
    fig_shap_dep.show()

    return pipe, preprocessor

# Load and preprocess data
train_url = 'https://raw.githubusercontent.com/Titanic-minds-group-14/Kaggle-challenge-group-14-/refs/heads/main/Data/train.csv'
test_url = 'https://raw.githubusercontent.com/Titanic-minds-group-14/Kaggle-challenge-group-14-/refs/heads/main/Data/test.csv'
train_df = pd.read_csv(train_url)
test_df = pd.read_csv(test_url)

# Define columns
numerical_cols = ['Age', 'RoomService', 'FoodCourt', 'ShoppingMall', 'Spa', 'VRDeck', 'Total_Spending']
categorical_cols = ['HomePlanet', 'CryoSleep', 'Destination', 'VIP', 'Deck', 'Side', 'IsSolo', 'GroupSize']
target_col = 'Transported'

# Preprocess data
train_df = preprocess_data(train_df, is_train=True)
test_df = preprocess_data(test_df)

# Verify columns in train and test data
print("Train columns:", train_df.columns.tolist())
print("Test columns:", test_df.columns.tolist())

# Train the model and generate SHAP plots
model, preprocessor = apply_shap_explanations(
    df=train_df,
    target_col=target_col,
    numerical_cols=numerical_cols,
    categorical_cols=categorical_cols
)

# Generate predictions on test data
test_features = test_df.drop(columns=['PassengerId'])
# The model is a pipeline that includes the preprocessor, so we pass the unprocessed test data to it.
y_pred = model.predict(test_features)

# Preparing the Kaggle submission file
submission = pd.DataFrame({'PassengerId': test_df['PassengerId'], 'Transported': y_pred})
submission['Transported'] = submission['Transported'].replace({0: False, 1: True})
submission.to_csv('submission_Test.csv', index=False)
files.download('submission_Test.csv')

Train columns: ['PassengerId', 'Age', 'RoomService', 'FoodCourt', 'ShoppingMall', 'Spa', 'VRDeck', 'Total_Spending', 'HomePlanet', 'CryoSleep', 'Destination', 'VIP', 'Deck', 'Side', 'IsSolo', 'GroupSize', 'Transported']
Test columns: ['PassengerId', 'Age', 'RoomService', 'FoodCourt', 'ShoppingMall', 'Spa', 'VRDeck', 'Total_Spending', 'HomePlanet', 'CryoSleep', 'Destination', 'VIP', 'Deck', 'Side', 'IsSolo', 'GroupSize']
Computing SHAP values for CatBoost...
Number of features after preprocessing: 37
Feature names: ['Age', 'RoomService', 'FoodCourt', 'ShoppingMall', 'Spa', 'VRDeck', 'Total_Spending', 'HomePlanet_Earth', 'HomePlanet_Europa', 'HomePlanet_Mars', 'CryoSleep_False', 'CryoSleep_True', 'Destination_55 Cancri e', 'Destination_PSO J318.5-22', 'Destination_TRAPPIST-1e', 'VIP_False', 'VIP_True', 'Deck_A', 'Deck_B', 'Deck_C', 'Deck_D', 'Deck_E', 'Deck_F', 'Deck_G', 'Deck_T', 'Side_P', 'Side_S', 'IsSolo_False', 'IsSolo_True', 'GroupSize_1', 'GroupSize_2', 'GroupSize_3', 'GroupSize_4

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>